In [1]:
#-*-coding:utf8-*-

"""
author:YJM

date:20190420

util function

"""
import os
import sys
import numpy as np
import pandas as pd
import operator

### 通过movies.csv获取电影信息

In [2]:
def get_item_info(input_file):
    if not os.path.exists(input_file):
        return {}
    item_info={}
    linenum=0
    fp = open(input_file)
    for line in fp:
        if linenum == 0:
            linenum += 1
            continue
        item = line.strip().split(',')
        if len(item)<3:
            continue
        elif len(item) == 3:
            itemid,title,genre = item[0],item[1],item[2]
        elif len(item)>3:
            itemid = item[0]
            genre = item[1]
            title = ','.join(item[1:-1])
        item_info[itemid]=[title,genre]
    fp.closed
    return item_info

### 通过ratings15000.csv获取平均分

In [3]:
def get_ave_score(input_file):
    if not os.path.exists(input_file):
        return {}
    linenum = 0
    record_dict = {}
    score_dict = {}
    fp = open(input_file)
    for line in fp:
        if linenum == 0:
            linenum += 1
            continue
        item = line.strip().split(',')
        if len(item)<4:
            continue
        userid,itemid,rating = item[0],item[1],float(item[2])
        if itemid not in record_dict:
            record_dict[itemid]=[0,0]
        record_dict[itemid][0] += 1
        record_dict[itemid][1] += rating
    fp.closed
    for itemid in record_dict:
        score_dict[itemid] = round(record_dict[itemid][1]/record_dict[itemid][0],3)#小数点后保留3位有效数字
    return score_dict

### 获取数据

In [4]:
def get_train_data(input_file):
    """
    :param input_file:
    input_file:user item rating file
    :return:
    alist:[(userid,itemid,label),(userid,itemid,label)]
    """
    if not os.path.exists(input_file):
        return {}
    score_dict = get_ave_score(input_file)#通过前面的方法获取平均分
    neg_dict = {}#负样本集合
    pos_dict = {}#正样本集合
    train_data = []
    linenum = 0
    score_thr = 4#正负分界线：4分
    fp = open(input_file)
    for line in fp:
        if linenum == 0:
            linenum += 1
            continue
        item = line.strip().split(',')
        if len(item)<4:
            continue
        userid,itemid,rating = item[0],item[1],float(item[2])
        if userid not in pos_dict:
            pos_dict[userid] = []
        if userid not in neg_dict:
            neg_dict[userid] = []
        if rating >=score_thr:
            pos_dict[userid].append((itemid,1))#这里正样本的格式是（userid，itemid，1）1代表正样本
        else:
            score = score_dict.get(itemid,0)#如果平均分没有获取到就设置成0
            neg_dict[userid].append((itemid,score))#这里负样本的格式是（userid，itemid，平均得分）    
    fp.closed
    for userid in pos_dict:
        data_num = min(len(pos_dict[userid]),len(neg_dict.get(userid,[])))
        if data_num > 0:
            train_data += [(userid,zuhe[0],zuhe[1]) for zuhe in pos_dict[userid]][:data_num]
        else:
            continue
        #将负样本倒序排好并且取和正样本同样大小的样本集合
        sorted_neg_list = sorted(neg_dict[userid],key=lambda element:element[1], reverse=True)[:data_num]
        train_data += [(userid,zuhe[0],0)for zuhe in sorted_neg_list]#将最后一个值替换成0
    return train_data

### 将lfm的模型进行训练

In [5]:
def lfm_train(train_data,F,alpha,beta,step):
    user_vec = {}
    item_vec = {}
    for step_index in range(step):#迭代轮次
        for data_instance in train_data:
            userid,itemid,label = data_instance
            if userid not in user_vec:
                user_vec[userid] = init_model(F)
            if itemid not in item_vec:
                item_vec[itemid] = init_model(F)
            delta = label - model_predict(user_vec[userid],item_vec[itemid])
            for index in range(F):
                user_vec[userid][index] += beta*(delta*item_vec[itemid][index]-alpha*user_vec[userid][index])
                item_vec[itemid][index] += beta*(delta*user_vec[userid][index]-alpha*item_vec[itemid][index])
            beta = beta*0.9      #学习率衰减
    return user_vec,item_vec

### 初始化模型

In [6]:
def init_model(vector_len):
    """
        vector_len:the len of vector
    """
    return np.random.randn(vector_len)

### 计算用户向量和物品向量的余弦夹角

In [7]:
def model_predict(user_vector,item_vector):
    res = np.dot(user_vector,item_vector)/(np.linalg.norm(user_vector)*np.linalg.norm(item_vector))
    return res

### 模型训练函数

In [14]:
def model_train_process():
    train_data = get_train_data("../data/ratings15000.csv")
    user_vec,item_vec = lfm_train(train_data,50,0.01,0.1,50)
    recom_result = give_recom_result(user_vec,item_vec,'24')
    print recom_result
    ana_recom_result(train_data,'24',recom_result)

### 模型训练执行

In [19]:
model_train_process()

[('73', 25.923), ('5284', 23.623), ('4166', 21.547), ('1391', 21.06), ('370', 20.869), ('4920', 19.668), ('5943', 19.566), ('653', 19.332), ('2291', 19.279), ('742', 18.911)]
['Toy Story (1995)', 'Adventure|Animation|Children|Comedy|Fantasy']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
['Heat (1995)', 'Action|Crime|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 3

['Thinner (1996)', 'Horror|Thriller']
['Big Daddy (1999)', 'Comedy']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
['"South Park: Bigger, Longer and Uncut (1999)"', '"South Park: Bigger']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonhea

['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, 

['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series

['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked 

...

['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, 

['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked 

['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked 

['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series

['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush (2001)', 'Comedy|Romance']
['Series 7: The Contenders (2001)', 'Action|Drama']
['Mars Attacks! (1996)', 'Action|Comedy|Sci-Fi']
['Naked Gun 33 1/3: The Final Insult (1994)', 'Action|Comedy']
['"Now, Voyager (1942)"', '"Now']
['Maid in Manhattan (2002)', 'Comedy|Romance']
['Dragonheart (1996)', 'Action|Adventure|Fantasy']
['Edward Scissorhands (1990)', 'Drama|Fantasy|Romance']
['Thinner (1996)', 'Horror|Thriller']
recom result
['"Mis\xc3\xa9rables, Les (1995)"', '"Mis\xc3\xa9rables']
['Crush 

### 推荐过程

In [18]:
def give_recom_result(user_vec,item_vec,userid):
    fix_num = 10
    if userid not in user_vec:
        return []
    record = {}
    recom_list = []
    user_vector = user_vec[userid]
    for itemid in item_vec:
        item_vector = item_vec[itemid]
        res = np.dot(user_vector,item_vector)/(np.linalg.norm(user_vector))*(np.linalg.norm(item_vector))
        record[itemid] = res
    for zuhe in sorted(record.iteritems(),key=operator.itemgetter(1),reverse=True)[:fix_num]:
        itemid = zuhe[0]
        score = round(zuhe[1],3)
        recom_list.append((itemid,score))
    return recom_list                                                                            

### 评估推荐结果

In [11]:
def ana_recom_result(train_data,userid,recom_list):
    item_info = get_item_info("../data/movies.csv")
    for data_instance in train_data:
        tmp_userid,itemid,label = data_instance
        if label == 1 and tmp_userid == userid:
            print item_info[itemid]
        print "recom result"
        for zuhe in recom_list:
            print item_info[zuhe[0]]